In [1]:
import re

In [2]:
vehicles_file = '/cluster/home/mfrancesc/IVT/5km_100pct/drt_vehicles_20000_4.xml'

In [3]:
with open(vehicles_file) as f:
    text = f.read()

In [4]:
start_links = [f[12:-1] for f in re.findall( 'start_link="[0-9]*"',text)]

In [6]:
len(start_links)

20000

In [7]:
network_file = '/cluster/home/mfrancesc/IVT/5km_100pct/zurich_network.xml.gz'

In [8]:
import gzip
import xml.etree.ElementTree as ET

a = gzip.open(network_file, 'r')
tree = ET.parse(a)
root = tree.getroot()

In [9]:
nodes = {}
for n in root.findall('nodes')[0].findall('node'):
    nodes[n.attrib['id']] = (float(n.attrib['x']), float(n.attrib['y']))

In [11]:
links = {}
for l in root.findall('links')[0].findall('link'):
    origin = nodes[l.attrib['from']]
    dest = nodes[l.attrib['to']]
    links[l.attrib['id']] = tuple([sum(x)/2 for x in zip(origin,dest)])

In [12]:
start_positions = [links[s] for s in start_links]

In [13]:
len(start_positions)

20000

In [14]:
import geopandas as gpd
import pandas as pd

In [15]:
df = pd.DataFrame(start_positions, columns=['x','y'])

In [16]:
gdf = gpd.GeoDataFrame(
    df, geometry=gpd.points_from_xy(df.x, df.y))
gdf.crs = 'EPSG:2056'

In [17]:
gdf.explore()

/cluster/apps/nss/gcc-8.2.0/python/3.10.4/x86_64/lib64/python3.10/site-packages/mapclassify/classifiers.py:511: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  def _fisher_jenks_means(values, classes=5, sort=True):


In [18]:
shp = gpd.read_file('/cluster/work/ivt_vpl/mfrancesc/ScenarioBoundary/zurich_city_5km.shp')

In [19]:
shp.explore()